In [3]:
import pandas as pd
from pymongo import MongoClient
import jieba
import re
import json

In [6]:
# 讀取MongoDB連線資訊
MongoDBInformation = json.load(open('./MongoDB_Information.txt', 'r'))

In [7]:
# 建立 MongoDB 數據庫連接 IP='10.1.16.67', port=27017
uri = 'mongodb://{}:{}@18.183.16.220:27017/?authSource=admin&readPreference=primary&appname=MongoDB%20Compass&ssl=false'\
    .format(MongoDBInformation['host'],MongoDBInformation['passwd'])
client = MongoClient(uri)
db = client['Recipe_OriginData']
collection = db['icook']

# find 回來的物件是 pymongo 的物件 需做轉換才可以使用
cursor = list(collection.find())

df = pd.DataFrame(cursor)

In [8]:
df.head()

_id RecipeID CategoryName SubCategoryID  \
0  60646cc365cd68e35c01e814   170303         家常菜色           104   
1  60646cc365cd68e35c01e815   169048         家常菜色           104   
2  60646cc365cd68e35c01e816   155271         家常菜色           104   
3  60646cc365cd68e35c01e817    90086         家常菜色           104   
4  60646cc365cd68e35c01e818   337797         家常菜色           104   

  SubCategoryName RecipeName  \
0              烤肉     綜合雞肉串燒   
1              烤肉  燒烤味增秋葵透抽捲   
2              烤肉     沙嗲烤雞肉串   
3              烤肉      甜柿烤肉串   
4              烤肉      韓式烤肉飯   

                                         Description          AuthorID  \
0  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   100002279834418   
1  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...     charminglydia   
2  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...      MrsPsKitchen   
3   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   jj5colorkitchen   
4  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...  1f2cb7b4bee5e7d2   

            Author Servings CookingTime  \
0              胖仙女      4人份        45分鐘   
1              懶廚房      2人份        20分鐘   
2  Mrs P's Kitchen      4人份        45分鐘   
3            jj5色廚      3人份        30分鐘   
4             幸福餐桌      2人份        45分鐘   

                                          Ingredient  \
0  {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
1  {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
2  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
3  {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
4  {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   

                                        CookingSteps LikeStat    Datetime  \
0  [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...      662  2016-09-11   
1  [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...      675  2016-09-01   
2  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
3  [1. 這種豬肉片就是平常酸菜白肉鍋用的白肉片，等於沒薰過的培根肉，形狀規則，油脂豐富，比一...      671  2014-10-25   
4  [1. 以刀背將牛肉片敲打鬆軟, 2. 牛肉片切成小塊狀, 3. 將蒜、奇異果、蘋果、洋蔥放...       53  2020-05-23   

     Preview                              URL  
0   2.4 萬 瀏覽  https://icook.tw/recipes/170303  
1   1.7 萬 瀏覽  https://icook.tw/recipes/169048  
2   3.3 萬 瀏覽  https://icook.tw/recipes/155271  
3   1.8 萬 瀏覽   https://icook.tw/recipes/90086  
4  8,026  瀏覽  https://icook.tw/recipes/337797

In [5]:
# 做一個全形轉半形的 function
def strQ2B(s):
    """把字串全形轉半形"""
    rstring = ""
    for uchar in s:
        u_code = ord(uchar)
        if u_code == 12288:  # 全形空格直接轉換
            u_code = 32
        elif 65281 <= u_code <= 65374:  # 全形字元（除空格）根據關係轉化
            u_code -= 65248
        rstring += chr(u_code)
    return rstring

In [6]:
df['Ingredient_Pro'] = 0
import cn2an

for n , Ingredients in enumerate(df['Ingredient']):
    TmpDict = dict()
    for EachIngredient in Ingredients.items(): # (食材名稱, 數量單位)
        
        # 使用正規表示法將食材名稱有特殊符號先處理:
        EachIngredientName = re.sub(r'(\(.*\))', '', EachIngredient[0]) # 有括號內的文字刪除
        EachIngredientName = re.sub(r'[\W+]', '', EachIngredientName)  # 特殊符號刪除
        
        # 將數量及特殊符號有包含全形字轉半形
        EachIngredientUnit = strQ2B(EachIngredient[1])

        try: 
            # 將非自尾出現'兩'的字，轉換成數字 2(字尾是"兩'"為量詞，不取代)
            if EachIngredientUnit[-1] != '兩':
                EachIngredientUnit = EachIngredientUnit.replace('兩','2')
        except IndexError:  # 部分資料有食材名稱但是沒有分量，所以會出現空 list，會有IndexError
            pass
        
      
        # 將漢字數字轉換成阿拉伯 (EX. 四 => 4)
        EachIngredientUnit = cn2an.transform(EachIngredientUnit, "cn2an")
        
        
        # 將數量統一用阿拉伯數字表示
        EachIngredientUnit = EachIngredientUnit.replace(' ','').replace('4/1','0.25').replace('2/1','0.5')\
        .replace('1/2','0.5').replace('1/3','0.25').replace('1/4','0.25').replace('1/5', '0.2').replace('1/6', '0.17')\
        .replace('1/7', '0.14').replace('1/8', '0.13').replace('4分之1','0.25').replace('2分之1','0.5').replace('3分之1','0.33')\
        .replace('5分之1','0.2').replace('3分之2','0.66').replace('6分之1','0.17').replace('4分之3','0.75').replace('½','0.5')\
        .replace('¼','0.25').replace('半', '0.5')
        
        
        # 使用正規表示法將數量及量詞有括號內的文字刪除
        EachIngredientUnit = re.sub(r'(\(.*)', '', EachIngredientUnit)
        
        # 使用正規表示法將數量及量詞分開(按數字做切割)
        EachIngredientUnitList = re.split(r'(\D+)',EachIngredientUnit)
        del EachIngredientUnitList[-1]  # 切開最後會多一個空字串，將其刪除
        
        # 將已經斷詞後的list 取最後一個當作量詞，前面的都當作數量(在合併成list)
        try:
            a = ''.join(EachIngredientUnitList[:-1])       
            b = ''.join(EachIngredientUnitList[-1])
            EachIngredientUnitList = [a,b]
        except IndexError:
            pass
        
        # 判斷數量及單位，若為空值
        if EachIngredientUnitList == []:
            EachIngredientUnitList = [1, '適量']
        if EachIngredientUnitList[0] == '':
            EachIngredientUnitList[0] = '1'  
            
        TmpDict.setdefault(EachIngredientName, EachIngredientUnitList) # 將 {食材:[數量,單位]} 加入字典
    df.loc[n, 'Ingredient_Pro'] = str(TmpDict)
    print(TmpDict)        
    print('----------')

{'去骨雞腿': ['4', '片'], '起士明太子醬': ['1', '適量'], '蔥白': ['1', '適量'], '檸檬': ['1', '適量'], '七味唐辛子粉': ['1', '適量'], '米酒或清酒': ['2', '大匙'], '海鹽': ['1', '大匙'], '醬油膏': ['2', '大匙'], '味醂': ['1', '大匙'], '水果醋': ['1', '大匙']}
----------
{'透抽': ['1', '尾'], '黃秋葵': ['6', '個'], '味增燒烤醬': ['1', '適量'], '白芝麻': ['1', '適量']}
----------
{'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油': ['1', '小匙'], '糖': ['1', '大匙'], '香油': ['1', '大匙'], '白胡椒粉': ['1', '少許'], '奶油': ['25', '克'], '蒜末': ['1', '小匙'], '花生醬': ['2', '小匙'], '豆瓣醬可省略': ['1', '小匙'], '水': ['120', '毫升'], '椰漿': ['120', '毫升']}
----------
{'火鍋白肉片': ['6-7', '片'], '甜柿': ['1', '顆'], '百里香': ['1', '適量'], '鹽': ['1', '適量'], '黑胡椒': ['1', '適量'], '太白粉': ['1', '少許'], '油': ['1', '茶匙']}
----------
{'沙朗牛肉片': ['400', '克'], '蒜': ['3', '瓣'], '洋蔥': ['1', '顆'], '蘋果': ['0.25', '顆'], '奇異果': ['1', '顆'], '薑泥': ['0.5', '茶匙'], '蜂蜜': ['2', '大匙'], '糖': ['2', '大匙'], '白酒': ['1', '大匙'], '醬油': ['80', '毫升'], '玉米粉': ['1', '大匙'], '芝麻油': ['0.5', '茶匙']}
----------
{'烤肉醬': ['1', '酌量'], '牛肉片': ['20', '片'], '蘆筍

{'雞胸肉': ['500', 'g'], '普通麵粉': ['150', 'g'], '蛋白': ['1', '顆'], '鹽巴': ['2', '茶匙'], '胡椒粉': ['1', '茶匙'], '清水': ['200', 'g'], '蛋黃': ['1', '顆'], '泡打粉': ['5', 'g']}
----------
{'檸檬片': ['6', '片'], '青椒黃椒紅椒': ['1', '顆'], '地瓜': ['1', '條'], '茄子': ['0.5', '條'], '蘆筍': ['4', '根'], '披薩塊冷凍食品': ['1', '可有可無'], '百葉豆腐': ['6', '塊'], '蝦子': ['6', '隻'], '雞塊': ['4', '個'], '醃雞肉鹹酥雞': ['7', '塊'], '酥炸粉': ['1', '大碗'], '地瓜粉': ['1', '大碗'], '蘋果泥取代蘿蔔泥': ['1', '顆'], '蔥花': ['1', '把'], '柚子胡椒製造清香嗆辣': ['1', '茶匙'], '醬油有點鹹': ['1', '適量'], '煲仔飯醬油有點甜': ['1', '適量']}
----------
{'糯米粉': ['150', 'g'], '紫薯鬆餅粉': ['50', 'g'], '麥芽糖': ['50', 'g'], '糖': ['25', 'g'], '水': ['125', 'g'], '紫薯濃縮液': ['2', '滴']}
----------
{'年糕': ['200', 'g'], '牛肉片': ['100', 'g'], '魚丸': ['6', '顆'], '蔥花': ['2', 'T'], '蒜末': ['1', 'T'], '洋蔥絲': ['1', '把'], '醬油': ['1.5', 'T'], '糖': ['0.5', 'T'], '水': ['2', 'T'], '米酒': ['0.5', 'T'], '胡椒粉': ['1', '少許'], '甜椒': ['0.5', '顆'], '紅蘿蔔': ['0.25', '條']}
----------
{'雞腿肉帶皮或去皮皆可': ['2', '大塊'], '地瓜粉': ['1', '適量'], '菜籽油或橄欖油': ['1', 

{'雞胸肉': ['300', '公克'], '九層塔': ['1', '適量'], '木薯粉或地瓜粉': ['150', '公克'], '豆腐乳': ['2', '塊'], '醬油': ['1', '大匙'], '糖': ['1', '小匙'], '米酒': ['1', '小匙'], '白胡椒粉': ['1', '小匙'], '五香粉': ['1', '小匙']}
----------
{'中卷約300克': ['1', '隻'], '檸檬': ['0.5', '顆'], '蛋': ['2', '顆'], '中筋麵粉': ['100', '克'], '地瓜粉': ['50', '克'], '咖喱粉': ['1', '大匙'], '起司粉': ['1', '大匙'], '五香粉': ['1', '小匙'], '鹽': ['1', '小匙'], '西洋芹菜': ['1', '適量'], '白胡椒粉': ['1', '適量']}
----------
{'花枝漿': ['0.5', '斤'], '白刺蝦仁': ['0.5', '斤'], '馬蹄仁': ['200', '公克'], '豆腐衣': ['4', '張'], '小黃瓜': ['3', '條'], '鹽': ['0.5', '小匙'], '白醋': ['2', '大匙'], '糖': ['2', '大匙'], '五香粉': ['1', '小匙'], '胡椒粉': ['0.5', '小匙'], '甜辣醬': ['1', '適量']}
----------
{'大顆馬鈴薯': ['2', '大顆'], '油炸油': ['500', 'ml'], '胡椒鹽': ['1', '少許'], '蕃茄醬': ['2', '大匙']}
----------
{'梅花肉': ['300', 'g'], '蛋': ['1', '顆'], '味醂': ['1', '大匙'], '米酒': ['1', '大匙'], '糖': ['1', '大匙'], '味噌': ['50', 'g'], '麵包粉': ['1', '適量'], '高麗菜絲': ['1', '適量'], '低筋麵粉': ['1', '適量'], '胡椒粉': ['1', '適量']}
----------
{'新鮮香菇': ['8', '朵'], '麵粉': ['1', 

{'白飯': ['2', '小碗'], '起司': ['25', 'g'], '洋蔥丁': ['約100', 'g'], '洋菇': ['2-3', '朵'], '杏鮑菇': ['2-3', '朵'], '彩椒': ['約1', '小碗'], '菠菜': ['1', '適量'], '鹽': ['0.25', '小匙'], '胡椒': ['0.25', '小匙'], '白酒': ['40', 'ml'], '紅甜椒粉可不加': ['0.25', '小匙'], '紅甜椒': ['1', '顆'], '蒜頭': ['3', '瓣'], '鮮奶油': ['50', 'ml'], '怡君有點辣萬用醬': ['1', '大匙']}
----------
{'馬鈴薯': ['1', '顆'], '奶油': ['1', '少許'], '起司': ['1', '少許'], '香料胡椒鹽': ['1', '少許']}
----------
{'千張皮2422': ['2', '片'], '地瓜泥': ['2', '條中等大小'], '乳酪絲': ['1', '適量']}
----------
{'彩椒': [1, '適量'], '絞肉': ['20', '元份量'], '洋蔥': ['0', '.'], '乳酪絲': ['1', '適量'], '蒜末': ['1', '適量'], '辣椒': ['1', '適量'], '黑胡椒': ['1', '少許'], '白胡椒粉': ['1', '少許'], '米酒': ['0.5', '個瓶蓋'], '醬油': ['0.5', '湯匙'], '橄欖油': ['5', 'cc']}
----------
{'大香菇': ['6', '朵'], '莫茲瑞拉起司片': ['2', '片'], '雞雞肉泥': ['75', 'g'], '馬鈴薯': ['75', 'g'], '紅蘿蔔末': ['10', 'g'], '洋蔥': ['15', 'g'], '雞蛋': ['1', '顆'], '玉米粉': ['2', '大匙*'], '酒': ['1', '大匙'], '鹽': ['1', '適量'], '黑胡椒': ['1', '適量'], '義式香料': ['1', '適量'], '麵粉': ['1', '少許']}
----------
{'豬絞肉'

{'馬鈴薯': ['2', '顆'], '美乃滋': ['1', '適量'], '玉米': ['1', '適量'], '火腿': ['1', '適量']}
----------
{'美國或澳洲馬鈴薯較適合': ['5', '個'], '培根片切小塊': ['1', '包'], '中型洋蔥切丁': ['3', '顆'], '圓形Reblochon': ['1', '個'], '鮮奶油CrèmeFraîche': ['2', '大匙'], '白酒': ['1', '杯'], '鹽和黑胡椒': ['1', '適量']}
----------
{'馬鈴薯': ['1', '個'], '洋蔥': ['0.5', '個'], '無鹽奶油': ['25', 'G'], '培根': ['1', '適量'], '黑胡椒': ['1', '適量'], '鹽': ['1', '適量'], '糖': ['1', '適量']}
----------
{'鮭魚': ['1', '酌量'], '杏鮑菇': ['0.5', '支'], '蔥': ['1', '支'], '塩': ['1', '酌量'], '胡椒粉': ['1', '酌量'], '起司絲': ['1', '酌量'], '洋香菜': ['1', '少許'], '紅蘿蔔': ['1', '數片'], '蛋': ['1', '個']}
----------
{'馬鈴薯中小型': ['1', '顆'], '培根': ['3', '片'], '起司絲': ['1', '把'], '咖哩粉': ['1', '茶匙'], '鹽巴': ['1', '少許'], '黑胡椒': ['1', '少許'], '百里香香料': ['1', '少許']}
----------
{'泡菜水餃': ['12', '顆'], '乳酪絲': ['1', '適量'], '韓式泡菜': ['1', '適量'], '起司': ['2', '片'], 'Dowai氣炸鍋': ['1', '台']}
----------
{'義大利麵': ['2', '人分'], '義大利肉醬': ['4', '大匙'], '乳酪絲': ['1', '適量']}
----------
{'地瓜': ['4', '塊'], '起司': ['1', '把']}
----------
{'豬扒': 

...

{'中筋麵粉': ['140', 'g'], '無糖可可粉': ['1', 'tbsp'], '白糖': ['2', 'tbsp'], '鹽': ['0.5', 'tsp'], '無鹽奶油冷藏狀': ['60', 'g'], '白酥油': ['2', 'tbsp'], '蛋黃': ['1', '顆'], '冷水': ['3', 'tbsp'], '澳洲果仁': ['24', '顆'], '烘焙用巧克力豆': ['0.5', '杯'], '奶油': ['0.5', 'tbsp']}
----------
{'低筋麵粉': ['100', 'g'], '砂糖': ['50', 'g'], '無鹽奶油': ['100', 'g'], '雞蛋': ['2', '顆'], '紅色色素或草莓粉': ['1', '適量'], '香草精': ['1', '茶匙']}
----------
{'去核黑棗': ['20', '個'], '杏仁': ['20', '個'], '75可可脂巧克力': ['120', '克']}
----------
{'低筋麵粉': ['\u202880', 'g\u2028'], '砂糖': ['80', 'g\u2028'], '奶油': ['60', 'g\u2028'], '蛋': ['2', '顆\u2028'], '可可粉': ['20', 'g\u2028'], '泡打粉': ['\u20280.5', '茶匙\u2028'], '奶油乳酪': ['\u202880', 'g\u2028'], '糖粉': ['80', 'g\u2028'], '鹽': ['1', '小撮\u2028'], '水': ['20', 'ml\u2028']}
----------
{'莫薩里拉芝士球': ['1', '個'], '牛油果': ['1', '個'], '車厘茄': ['1', '小盒'], '西生菜': ['1', '個'], 'Balsamic醬': ['6', '湯匙'], '茄汁': ['2', '湯匙'], '代糖': ['1', '小包']}
----------
{'去骨雞腿': ['4', '份'], '青花菜': ['100', '克'], '小番茄': ['4', '顆'], '大蒜': ['1', '球'], '青蔥': ['1

{'豬腳': ['1', '隻'], '蒜頭': ['10', '瓣'], '薑': ['30', 'g'], '蔥': ['3', '根'], '八角': ['2', '粒'], '砂糖': ['1', '大匙'], '米酒': ['0.5', '杯'], '醬油': ['120', 'cc'], '水': ['1', '適量'], '滷味包': ['1', '份']}
----------
{'去核紅棗': ['250', '克'], '水': ['800', '毫升'], '香棗片糖': ['110', '克'], '木薯粉': ['85', '克'], '馬蹄粉': ['20', '克'], '糯米粉': ['40', '克'], '椰汁': ['100', '毫升'], '熱水': ['35', '毫升'], '砂糖': ['30', '克']}
----------
{'糯米粉': ['200', 'g'], '二砂糖': ['25', 'g'], '紅麴粉': ['2', 'g'], '水': ['145', 'g'], '紅豆': ['45', 'g'], '月桃葉': ['2', '片']}
----------
{'大白菜': ['1', '顆'], '紅蘿蔔': ['0.5', '條'], '黑木耳': ['1', '朵'], '乾香菇': ['6', '朵'], '老薑': ['8', '片'], '香菜': ['2', '株'], '冬粉': ['2', '把'], '枸杞': ['1', '茶匙'], '麻油': ['2', '茶匙'], '醬油': ['1', '大匙'], '烏醋': ['1.5', '茶匙'], '鹽': ['0.13', '茶匙'], '胡椒粉': ['0.13', '茶匙']}
----------
{'烏魚': ['1', '尾'], '大白菜': ['1', '顆'], '紅蘿蔔': ['0.25', '條'], '黑木耳': ['1', '大朵'], '香菇': ['3', '朵'], '排骨可有可無': ['4', '塊'], '洋蔥': ['1', '顆'], '蒜頭': ['2', '瓣'], '薑': ['5', '片'], '大蔥': ['1', '枝'], '鹽': ['0.5', '茶匙'],

{'綠咖哩牛肉': ['600', 'g'], '鴻禧菇': ['1', '大朵'], '泰式椰奶': ['250', 'ml'], '鮮奶': ['100', 'ml'], '有心泰式綠咖哩醬': ['1', '茶匙'], '嫩豆腐': ['1', '適量'], '綜合火鍋料': ['1', '適量'], '香菜末': ['1', '適量'], '大白菜': ['300', 'g'], '紅蘿蔔': ['1', '根'], '牛番茄': ['2', '個'], '玉米': ['1', '根']}
----------
{'水': ['1500', 'cc'], '鰹魚粉': ['5', 'g'], '味噌': ['1', '適量'], '高麗菜': ['0.5', '顆'], '玉米': ['1', '條'], '蝦子蛤蠣': ['1', '適量'], '火鍋料': ['1', '適量'], '青菜': ['1', '適量']}
----------
{'紅薏仁蘿蔔糕': ['3', '片'], '紅蘿蔔': ['20', 'g'], '甜豌豆': ['4', '根'], '綠豆芽': ['1', '適量'], '芹菜': ['3', '根'], '豆乾': ['2', '片'], '香菇': ['1', '朵'], '金針菇': ['0.5', '包'], '香菜': ['2', '株']}
----------
{'馬蹄': ['3', '顆'], '馬蹄粉': ['90', '克'], '桂花': ['2', '湯匙'], '黃砂糖': ['80', '克'], '白砂糖': ['30', '克'], '水': ['450', 'ml'], '油': ['1', '少許']}
----------
{'豬梅花肉': ['200', '克'], '豬肚': ['1', '顆'], '沙拉筍': ['1', '個'], '酸菜': ['0.5', '個'], '紅蘿蔔': ['1', '根'], '胡瓜絲條': ['2', '條']}
----------
{'中型透抽': ['1', '隻'], '毛豆仁': ['2', '大匙'], '鹹蛋黃': ['8~10', '顆'], '米酒': ['0.5', '小匙'], '牙籤': ['2~3', '支'], 

{'柚子或文旦果肉': ['0.5', '顆'], '雞蛋': ['3', '粒'], '鹽巴': ['1', '少許'], '奶油或其他食用油': ['1', '少許']}
----------
{'二節翅': ['12', '個'], '紅椒粉': ['1', '大匙'], '香蒜粒': ['1', '大匙'], '鹽': ['1', '小匙'], '黑胡椒粗粒': ['1', '小匙'], '白酒': ['1', '小匙'], '麵粉': ['40', '公克'], '奶油': ['40', '公克'], '蒜末': ['1', '小匙'], 'Tabasco': ['2', '大匙'], '蕃茄醬': ['2', '大匙'], '蜂蜜': ['1', '小匙']}
----------
{'蒜頭': ['5~7', '瓣'], '薑塊': ['1', '約大拇哥尺寸'], '醬油膏': ['5', '大匙'], '蕃茄醬': ['2', '大匙'], '二砂糖ㄏ': ['2', '大匙'], '開水': ['0.25', '杯']}
----------
{'去骨雞腿肉': ['1、2', '隻'], '松阪豬': ['1', '塊'], '去骨牛小排': ['1', '盒'], '洋蔥': ['0.5', '個'], '青蔥': ['5', '根'], '鹽': ['0.5', '小匙'], '七味粉': ['1', '少許'], '檸檬': ['0.5', '顆']}
----------
{'水油皮成份如下': ['6', '份'], '中粉': ['60', 'g'], '糖': ['5', 'g'], '水': ['30', 'g'], '猪油': ['25', 'g'], '酥油皮成份如下': ['6', '份']}
----------
{'去骨雞腿肉': ['1、2', '隻'], '松阪豬': ['1', '塊'], '去骨牛小排': ['1', '盒'], '醬油': ['0.5', '碗'], '米酒': ['5', '大匙'], '味醂': ['5', '大匙'], '水': ['5', '大匙'], '白芝麻': ['1', '少許'], '七味粉': ['1', '少許']}
----------
{'鹹蛋黃': ['30顆剖0'

{'白豆沙': ['260', 'g'], '鹹蛋黃': ['6顆約90', 'g'], '米酒': ['1', '少許'], '中筋麵粉': ['116', 'g'], '糖': ['7', 'g'], '酥油': ['45', 'g'], '冷水': ['53', 'g'], '低筋麵粉': ['103', 'g']}
----------
{'羊肩排': ['500', 'g'], '橄欖油': ['1', '少許'], '麵包粉': ['100', 'g'], '腰果': ['60', 'g'], '迷迭香': ['1', '適量'], '鹽巴': ['0.5', '小匙'], '薄荷及優格': ['1', '少許'], '紅葡萄汁': ['500', 'cc'], '紅酒': ['500', 'cc'], '洋蔥': ['0.5', '顆'], '蒜頭': ['1', '適量'], '黑胡椒': ['0.5', '小匙']}
----------
{'去骨雞腿排': ['2', '片'], '蘋果西打': ['120', 'ml'], '檸檬汁': ['1-0.5', '大匙'], '蒜瓣': ['4', '瓣'], '辣椒': ['0.25', '根'], '小黃瓜': ['1', '根'], 'Laleli精選冷壓初榨橄欖油': ['1', '大匙'], '番茄醬': ['1-0.5', '大匙'], '太白粉': ['0.25', '茶匙'], '醬油': ['3-0.5', '大匙'], '醬油膏': ['1', '茶匙'], '胡椒鹽': ['0.25', '茶匙']}
----------
{'鹹蛋黃': ['20', '顆'], '含油烏豆沙': ['500', 'g'], '低筋麵粉': ['150', 'g'], '無水奶油': ['67', 'g'], '蛋黃液': ['50', 'g'], '黑芝麻': ['20', 'g'], '砂糖': ['20', 'g'], '水': ['90', 'g']}
----------
{'去骨雞腿肉': ['500', 'g'], '醬油': ['100', 'ml'], '味醂': ['100', 'ml'], '米酒': ['50', 'ml'], '水': ['50', 'ml'], '蒜

In [10]:
# unique()找出不重複的數值(會包含重複的，重複的只會列出一次)
len(df['RecipeID'].unique())

26179

In [11]:
# 製作一個dataframe 把不重複的資料接住(keep=False 代表只要表中出現重複，都不會保留)
df_unique = df.drop_duplicates(['RecipeID'], keep=False)
df_unique.head()

_id RecipeID CategoryName SubCategoryID  \
14  60646cc365cd68e35c01e822   265696         家常菜色           104   
24  60646cc365cd68e35c01e82c   258366         家常菜色           104   
43  60646da165cd68e35c01e83f   220646         家常菜色           104   
50  60646da165cd68e35c01e846   174663         家常菜色           104   
54  60646da165cd68e35c01e84a   165576         家常菜色           104   

   SubCategoryName         RecipeName  \
14              烤肉        香料烤雞佐花椒鳳梨果醬   
24              烤肉        五分鐘「韓式烤肉飯」❤   
43              烤肉    [蜂蜜檸檬紅茶烤雞翅]烤肉料理   
50              烤肉             韓式八色烤肉   
54              烤肉  超夯!三色韓國烤肉!五花肉大變身!   

                                          Description         AuthorID  \
14  簡單步驟，人見人愛的烤雞串燒就能端上桌 ! 搭配微酸清爽的台灣在地花椒鳳梨果醬，更瞬間豐富了...              GFU   
24  這天看了尹食堂就動手做個簡單的「韓式烤肉飯」♡\n湯汁好下飯而且五分鐘就能完成!!!\n更多...  100002651431163   
43  市面上賣的烤肉醬重鹹重油，味道濃厚，吃了容易膩。這道蜂蜜檸檬紅茶烤雞翅用紅茶、檸檬去肉腥，並...      julia777777   
50  韓國吹來一股烤肉風，用八款不同顏色的醬料醃漬，用油花分布均勻的松阪豬替代五花肉，放在烤盤上滋...          nicosun   
54  最近很夯的韓國多色烤肉，訂位電話永遠打不通～但其實只要花點心思，不用再癡癡排隊等候，中秋節在...        710728454   

              Author Servings CookingTime  \
14  GoodFoodYou 料理庫       4人份        15分鐘   
24        Popo Huang      3人份         5分鐘   
43             朱麗安廚房      4人份        45分鐘   
50         時尚煮婦 Nico      4人份        30分鐘   
54            雀喜廚房日記      4人份        20分鐘   

                                           Ingredient  \
14  {'去骨雞腿肉': '400g', '摩洛哥綜合香料': '1茶匙', '橄欖油': '適量...   
24  {'牛肉': '350g', '韓式烤肉醬': '3-5大匙', '豆芽菜': '適量', ...   
43  {'雞翅': '7隻', '黑胡椒粒': '少許', '蜂蜜': '適量', '匈牙利辣椒粉...   
50  {'松阪豬': '500G', '泡菜': '20g', '黑胡椒': '20g', '加哩...   
54  {'豬五花肉': '3條', '蘿蔓生菜': '2顆', '生大蒜片': '適量', '韓國...   

                                         CookingSteps LikeStat    Datetime  \
14  [1. 雞腿以摩洛哥綜合香料、橄欖油、檸檬汁與切碎的大蒜醃漬半小時。\n將醃漬好的雞肉用竹籤...      167  2018-09-01   
24  [1. 在鍋中倒入麻油後加入牛肉拌炒。, 2. 稍微翻炒一下牛肉。, 3. 導熱效果很好所以...      268  2018-07-04   
43  [1. 取一鍋放水200cc，水滾熄火，放紅茶包及全部烤肉醬材料，泡10分鐘後 取出茶包，放...      298  2017-09-13   
50  [1. 松阪豬肉切片分成八等份, 2. 食材準備:\n松阪豬500G\n1.泡菜醬汁 \n2...      420  2016-10-20   
54  [1. 醃五花肉變變變 !\n\n【原味烤肉】不做任何醃漬，最能品嘗豬肉鮮甜。\n【大蒜烤肉...      671  2016-08-02   

      Preview                              URL  \
14  3,021  瀏覽  https://icook.tw/recipes/265696   
24  4,882  瀏覽  https://icook.tw/recipes/258366   
43  5,040  瀏覽  https://icook.tw/recipes/220646   
50  8,436  瀏覽  https://icook.tw/recipes/174663   
54   4.7 萬 瀏覽  https://icook.tw/recipes/165576   

                                       Ingredient_Pro  
14  {'去骨雞腿肉': ['400', 'g'], '摩洛哥綜合香料': ['1', '茶匙']...  
24  {'牛肉': ['350', 'g'], '韓式烤肉醬': ['3-5', '大匙'], '...  
43  {'雞翅': ['7', '隻'], '黑胡椒粒': ['1', '少許'], '蜂蜜': ...  
50  {'松阪豬': ['500', 'G'], '泡菜': ['20', 'g'], '黑胡椒'...  
54  {'豬五花肉': ['3', '條'], '蘿蔓生菜': ['2', '顆'], '生大蒜片...

In [12]:
len(df_unique)

15671

In [13]:
# test
df[df['RecipeID']=='155271']

_id RecipeID CategoryName SubCategoryID  \
2      60646cc365cd68e35c01e816   155271         家常菜色           104   
34374  6068f16465cd68e35c026e5a   155271         時間場合            77   
40536  6069bee265cd68e35c02866c   155271         季節節慶           602   

      SubCategoryName RecipeName  \
2                  烤肉     沙嗲烤雞肉串   
34374              宵夜     沙嗲烤雞肉串   
40536            中秋料理     沙嗲烤雞肉串   

                                             Description      AuthorID  \
2      這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...  MrsPsKitchen   
34374  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...  MrsPsKitchen   
40536  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...  MrsPsKitchen   

                Author Servings CookingTime  \
2      Mrs P's Kitchen      4人份        45分鐘   
34374  Mrs P's Kitchen      4人份        45分鐘   
40536  Mrs P's Kitchen      4人份        45分鐘   

                                              Ingredient  \
2      {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
34374  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
40536  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   

                                            CookingSteps LikeStat    Datetime  \
2      [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
34374  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
40536  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   

        Preview                              URL  \
2      3.3 萬 瀏覽  https://icook.tw/recipes/155271   
34374  3.3 萬 瀏覽  https://icook.tw/recipes/155271   
40536  3.3 萬 瀏覽  https://icook.tw/recipes/155271   

                                          Ingredient_Pro  
2      {'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油':...  
34374  {'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油':...  
40536  {'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油':...

In [14]:
df[df['RecipeID'] == '155271'].index

Int64Index([2, 34374, 40536], dtype='int64')

In [16]:
# 針對有重複的部分，用另外的 df處理
df_duplicated = df.copy()
df_duplicated = df_duplicated[~df_duplicated['RecipeID'].isin(df_unique['RecipeID'])] #  ~ 用法 true => false , false => true
df_duplicated.head()

_id RecipeID CategoryName SubCategoryID  \
0  60646cc365cd68e35c01e814   170303         家常菜色           104   
1  60646cc365cd68e35c01e815   169048         家常菜色           104   
2  60646cc365cd68e35c01e816   155271         家常菜色           104   
3  60646cc365cd68e35c01e817    90086         家常菜色           104   
4  60646cc365cd68e35c01e818   337797         家常菜色           104   

  SubCategoryName RecipeName  \
0              烤肉     綜合雞肉串燒   
1              烤肉  燒烤味增秋葵透抽捲   
2              烤肉     沙嗲烤雞肉串   
3              烤肉      甜柿烤肉串   
4              烤肉      韓式烤肉飯   

                                         Description          AuthorID  \
0  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   100002279834418   
1  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...     charminglydia   
2  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...      MrsPsKitchen   
3   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   jj5colorkitchen   
4  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...  1f2cb7b4bee5e7d2   

            Author Servings CookingTime  \
0              胖仙女      4人份        45分鐘   
1              懶廚房      2人份        20分鐘   
2  Mrs P's Kitchen      4人份        45分鐘   
3            jj5色廚      3人份        30分鐘   
4             幸福餐桌      2人份        45分鐘   

                                          Ingredient  \
0  {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
1  {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
2  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
3  {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
4  {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   

                                        CookingSteps LikeStat    Datetime  \
0  [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...      662  2016-09-11   
1  [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...      675  2016-09-01   
2  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
3  [1. 這種豬肉片就是平常酸菜白肉鍋用的白肉片，等於沒薰過的培根肉，形狀規則，油脂豐富，比一...      671  2014-10-25   
4  [1. 以刀背將牛肉片敲打鬆軟, 2. 牛肉片切成小塊狀, 3. 將蒜、奇異果、蘋果、洋蔥放...       53  2020-05-23   

     Preview                              URL  \
0   2.4 萬 瀏覽  https://icook.tw/recipes/170303   
1   1.7 萬 瀏覽  https://icook.tw/recipes/169048   
2   3.3 萬 瀏覽  https://icook.tw/recipes/155271   
3   1.8 萬 瀏覽   https://icook.tw/recipes/90086   
4  8,026  瀏覽  https://icook.tw/recipes/337797   

                                      Ingredient_Pro  
0  {'去骨雞腿': ['4', '片'], '起士明太子醬': ['1', '適量'], '蔥...  
1  {'透抽': ['1', '尾'], '黃秋葵': ['6', '個'], '味增燒烤醬':...  
2  {'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油':...  
3  {'火鍋白肉片': ['6-7', '片'], '甜柿': ['1', '顆'], '百里香...  
4  {'沙朗牛肉片': ['400', '克'], '蒜': ['3', '瓣'], '洋蔥':...

In [17]:
# Check
print('df_unique:',len(df_unique))
print('df_duplicated:',len(df_duplicated))
print('df_duplicated+df_unique:',len(df_unique)+len(df_duplicated))
print('df:',len(df))

df_unique: 15671
df_duplicated: 24952
df_duplicated+df_unique: 40623
df: 40623


In [18]:
len(df_duplicated['RecipeID'].unique())

10508

In [19]:
df_duplicated['RecipeID'].unique()

array(['170303', '169048', '155271', ..., '49868', '279637', '136152'],
      dtype=object)

In [20]:
# 找出同一個重複食譜但有不同類別，將類別合併
for x in df_duplicated['RecipeID'].unique():
    a = [y for y in df_duplicated[df_duplicated['RecipeID']==x].index] # 抓出每個相同食譜的 index
    b = [z for z in df_duplicated.loc[a, 'SubCategoryID']]             # 根據相同食譜的index 抓出不同類別ID，並放在list內
    c = [v for v in df_duplicated.loc[a, 'SubCategoryName']]           # 根據相同食譜的index 抓出不同類別名稱，並放在list內
    df_duplicated.loc[a,'SubCategoryID'] = str(b)
    df_duplicated.loc[a,'SubCategoryName'] = str(c)

In [21]:
#test
df_duplicated.head()

_id RecipeID CategoryName         SubCategoryID  \
0  60646cc365cd68e35c01e814   170303         家常菜色        ['104', '602']   
1  60646cc365cd68e35c01e815   169048         家常菜色         ['104', '77']   
2  60646cc365cd68e35c01e816   155271         家常菜色  ['104', '77', '602']   
3  60646cc365cd68e35c01e817    90086         家常菜色        ['104', '602']   
4  60646cc365cd68e35c01e818   337797         家常菜色         ['104', '61']   

        SubCategoryName RecipeName  \
0        ['烤肉', '中秋料理']     綜合雞肉串燒   
1          ['烤肉', '宵夜']  燒烤味增秋葵透抽捲   
2  ['烤肉', '宵夜', '中秋料理']     沙嗲烤雞肉串   
3        ['烤肉', '中秋料理']      甜柿烤肉串   
4          ['烤肉', '韓式']      韓式烤肉飯   

                                         Description          AuthorID  \
0  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   100002279834418   
1  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...     charminglydia   
2  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...      MrsPsKitchen   
3   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   jj5colorkitchen   
4  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...  1f2cb7b4bee5e7d2   

            Author Servings CookingTime  \
0              胖仙女      4人份        45分鐘   
1              懶廚房      2人份        20分鐘   
2  Mrs P's Kitchen      4人份        45分鐘   
3            jj5色廚      3人份        30分鐘   
4             幸福餐桌      2人份        45分鐘   

                                          Ingredient  \
0  {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
1  {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
2  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
3  {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
4  {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   

                                        CookingSteps LikeStat    Datetime  \
0  [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...      662  2016-09-11   
1  [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...      675  2016-09-01   
2  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
3  [1. 這種豬肉片就是平常酸菜白肉鍋用的白肉片，等於沒薰過的培根肉，形狀規則，油脂豐富，比一...      671  2014-10-25   
4  [1. 以刀背將牛肉片敲打鬆軟, 2. 牛肉片切成小塊狀, 3. 將蒜、奇異果、蘋果、洋蔥放...       53  2020-05-23   

     Preview                              URL  \
0   2.4 萬 瀏覽  https://icook.tw/recipes/170303   
1   1.7 萬 瀏覽  https://icook.tw/recipes/169048   
2   3.3 萬 瀏覽  https://icook.tw/recipes/155271   
3   1.8 萬 瀏覽   https://icook.tw/recipes/90086   
4  8,026  瀏覽  https://icook.tw/recipes/337797   

                                      Ingredient_Pro  
0  {'去骨雞腿': ['4', '片'], '起士明太子醬': ['1', '適量'], '蔥...  
1  {'透抽': ['1', '尾'], '黃秋葵': ['6', '個'], '味增燒烤醬':...  
2  {'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油':...  
3  {'火鍋白肉片': ['6-7', '片'], '甜柿': ['1', '顆'], '百里香...  
4  {'沙朗牛肉片': ['400', '克'], '蒜': ['3', '瓣'], '洋蔥':...

In [22]:
# 刪除重複，保留第一個
df_duplicated = df_duplicated.drop_duplicates(['RecipeID'], keep='first')

In [23]:
df_duplicated.head()

_id RecipeID CategoryName         SubCategoryID  \
0  60646cc365cd68e35c01e814   170303         家常菜色        ['104', '602']   
1  60646cc365cd68e35c01e815   169048         家常菜色         ['104', '77']   
2  60646cc365cd68e35c01e816   155271         家常菜色  ['104', '77', '602']   
3  60646cc365cd68e35c01e817    90086         家常菜色        ['104', '602']   
4  60646cc365cd68e35c01e818   337797         家常菜色         ['104', '61']   

        SubCategoryName RecipeName  \
0        ['烤肉', '中秋料理']     綜合雞肉串燒   
1          ['烤肉', '宵夜']  燒烤味增秋葵透抽捲   
2  ['烤肉', '宵夜', '中秋料理']     沙嗲烤雞肉串   
3        ['烤肉', '中秋料理']      甜柿烤肉串   
4          ['烤肉', '韓式']      韓式烤肉飯   

                                         Description          AuthorID  \
0  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   100002279834418   
1  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...     charminglydia   
2  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...      MrsPsKitchen   
3   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   jj5colorkitchen   
4  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...  1f2cb7b4bee5e7d2   

            Author Servings CookingTime  \
0              胖仙女      4人份        45分鐘   
1              懶廚房      2人份        20分鐘   
2  Mrs P's Kitchen      4人份        45分鐘   
3            jj5色廚      3人份        30分鐘   
4             幸福餐桌      2人份        45分鐘   

                                          Ingredient  \
0  {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
1  {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
2  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
3  {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
4  {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   

                                        CookingSteps LikeStat    Datetime  \
0  [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...      662  2016-09-11   
1  [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...      675  2016-09-01   
2  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
3  [1. 這種豬肉片就是平常酸菜白肉鍋用的白肉片，等於沒薰過的培根肉，形狀規則，油脂豐富，比一...      671  2014-10-25   
4  [1. 以刀背將牛肉片敲打鬆軟, 2. 牛肉片切成小塊狀, 3. 將蒜、奇異果、蘋果、洋蔥放...       53  2020-05-23   

     Preview                              URL  \
0   2.4 萬 瀏覽  https://icook.tw/recipes/170303   
1   1.7 萬 瀏覽  https://icook.tw/recipes/169048   
2   3.3 萬 瀏覽  https://icook.tw/recipes/155271   
3   1.8 萬 瀏覽   https://icook.tw/recipes/90086   
4  8,026  瀏覽  https://icook.tw/recipes/337797   

                                      Ingredient_Pro  
0  {'去骨雞腿': ['4', '片'], '起士明太子醬': ['1', '適量'], '蔥...  
1  {'透抽': ['1', '尾'], '黃秋葵': ['6', '個'], '味增燒烤醬':...  
2  {'雞肉': ['600', '克'], '沙嗲醬': ['1', '大匙'], '醬油':...  
3  {'火鍋白肉片': ['6-7', '片'], '甜柿': ['1', '顆'], '百里香...  
4  {'沙朗牛肉片': ['400', '克'], '蒜': ['3', '瓣'], '洋蔥':...

In [24]:
# 將處理好的兩個 df 合併
df_merge = df_duplicated.append(df_unique)

In [25]:
df_merge

_id RecipeID CategoryName         SubCategoryID  \
0      60646cc365cd68e35c01e814   170303         家常菜色        ['104', '602']   
1      60646cc365cd68e35c01e815   169048         家常菜色         ['104', '77']   
2      60646cc365cd68e35c01e816   155271         家常菜色  ['104', '77', '602']   
3      60646cc365cd68e35c01e817    90086         家常菜色        ['104', '602']   
4      60646cc365cd68e35c01e818   337797         家常菜色         ['104', '61']   
...                         ...      ...          ...                   ...   
40617  6069c28e65cd68e35c0286bd    56309         季節節慶                   602   
40619  6069c28e65cd68e35c0286bf    55995         季節節慶                   602   
40620  6069c28e65cd68e35c0286c0    55992         季節節慶                   602   
40621  6069c28e65cd68e35c0286c1    55938         季節節慶                   602   
40622  6069c28e65cd68e35c0286c2    55572         季節節慶                   602   

            SubCategoryName RecipeName  \
0            ['烤肉', '中秋料理']     綜合雞肉串燒   
1              ['烤肉', '宵夜']  燒烤味增秋葵透抽捲   
2      ['烤肉', '宵夜', '中秋料理']     沙嗲烤雞肉串   
3            ['烤肉', '中秋料理']      甜柿烤肉串   
4              ['烤肉', '韓式']      韓式烤肉飯   
...                     ...        ...   
40617                  中秋料理        芋頭酥   
40619                  中秋料理      抹茶核桃酥   
40620                  中秋料理      抹茶地瓜酥   
40621                  中秋料理        蛋黃酥   
40622                  中秋料理      豆沙月餅餡   

                                             Description          AuthorID  \
0      用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   100002279834418   
1      秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...     charminglydia   
2      這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...      MrsPsKitchen   
3       霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   jj5colorkitchen   
4      百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...  1f2cb7b4bee5e7d2   
...                                                  ...               ...   
40617                    家人蒸了芋頭,但太乾了,所以我加奶油跟糖,做了酥餅,很好吃喔。   100000068389648   
40619                 愛料理食譜網中秋節到了，自己動手做月餅，美味又健康。送禮自用兩相宜喔               Obs   
40620             中秋節快到了,做點不一樣的月餅,剛好家裡蒸好的地瓜,把它當饀,家人都說好吃。   100000068389648   
40621                  中秋節到了,聽說外面的蛋黃酥很貴,自己做安心也沒負擔,還很好吃喔。   100000068389648   
40622                                 自製的豆沙少油少糖，吃得安心，沒負擔        1023977372   

                Author Servings CookingTime  \
0                  胖仙女      4人份        45分鐘   
1                  懶廚房      2人份        20分鐘   
2      Mrs P's Kitchen      4人份        45分鐘   
3                jj5色廚      3人份        30分鐘   
4                 幸福餐桌      2人份        45分鐘   
...                ...      ...         ...   
40617       Hank Chung      8人份        60分鐘   
40619              OBS      4人份        60分鐘   
40620       Hank Chung      7人份        60分鐘   
40621       Hank Chung     10人份        60分鐘   
40622         Fion Tan     10人份       180分鐘   

                                              Ingredient  \
0      {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
1      {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
2      {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
3      {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
4      {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   
...                                                  ...   
40617  {'中筋麵粉': '300g', '豬油': '120g', '糖': '20g', '水'...   
40619  {'紅豆': '300g', '水': '120cc', '糖': '30g', '奶油':...   
40620  {'中筋麵粉': '200g', '豬油': '70g', '水': '100g', '抹茶...   
40621  {'中筋麵粉': '300g', '豬油': '120g', '糖': '30g', '水'...   
40622  {'紅豆': '1000g', '水': '2500ml', '糖': '380g', '油...   

                                            CookingSteps LikeStat    Datetime  \
0      [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...      662  2016-09-11   
1      [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...      675  2016-09-01   
2      [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...    1,669  2016-06-02   
3      [1. 這種豬肉片就是平常酸菜白肉鍋用的

In [26]:
df_merge = df_merge.set_index('_id')

In [27]:
df_merge.head()

RecipeID CategoryName         SubCategoryID  \
_id                                                                    
60646cc365cd68e35c01e814   170303         家常菜色        ['104', '602']   
60646cc365cd68e35c01e815   169048         家常菜色         ['104', '77']   
60646cc365cd68e35c01e816   155271         家常菜色  ['104', '77', '602']   
60646cc365cd68e35c01e817    90086         家常菜色        ['104', '602']   
60646cc365cd68e35c01e818   337797         家常菜色         ['104', '61']   

                               SubCategoryName RecipeName  \
_id                                                         
60646cc365cd68e35c01e814        ['烤肉', '中秋料理']     綜合雞肉串燒   
60646cc365cd68e35c01e815          ['烤肉', '宵夜']  燒烤味增秋葵透抽捲   
60646cc365cd68e35c01e816  ['烤肉', '宵夜', '中秋料理']     沙嗲烤雞肉串   
60646cc365cd68e35c01e817        ['烤肉', '中秋料理']      甜柿烤肉串   
60646cc365cd68e35c01e818          ['烤肉', '韓式']      韓式烤肉飯   

                                                                Description  \
_id                                                                           
60646cc365cd68e35c01e814  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   
60646cc365cd68e35c01e815  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...   
60646cc365cd68e35c01e816  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...   
60646cc365cd68e35c01e817   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   
60646cc365cd68e35c01e818  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...   

                                  AuthorID           Author Servings  \
_id                                                                    
60646cc365cd68e35c01e814   100002279834418              胖仙女      4人份   
60646cc365cd68e35c01e815     charminglydia              懶廚房      2人份   
60646cc365cd68e35c01e816      MrsPsKitchen  Mrs P's Kitchen      4人份   
60646cc365cd68e35c01e817   jj5colorkitchen            jj5色廚      3人份   
60646cc365cd68e35c01e818  1f2cb7b4bee5e7d2             幸福餐桌      2人份   

                         CookingTime  \
_id                                    
60646cc365cd68e35c01e814        45分鐘   
60646cc365cd68e35c01e815        20分鐘   
60646cc365cd68e35c01e816        45分鐘   
60646cc365cd68e35c01e817        30分鐘   
60646cc365cd68e35c01e818        45分鐘   

                                                                 Ingredient  \
_id                                                                           
60646cc365cd68e35c01e814  {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
60646cc365cd68e35c01e815  {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
60646cc365cd68e35c01e816  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
60646cc365cd68e35c01e817  {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
60646cc365cd68e35c01e818  {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   

                                                               CookingSteps  \
_id                                                                           
60646cc365cd68e35c01e814  [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...   
60646cc365cd68e35c01e815  [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...   
60646cc365cd68e35c01e816  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...   
60646cc365cd68e35c01e817  [1. 這種豬肉片就是平常酸菜白肉鍋用的白肉片，等於沒薰過的培根肉，形狀規則，油脂豐富，比一...   
60646cc365cd68e35c01e818  [1. 以刀背將牛肉片敲打鬆軟, 2. 牛肉片切成小塊狀, 3. 將蒜、奇異果、蘋果、洋蔥放...   

                         LikeStat    Datetime    Preview  \
_id                                                        
60646cc365cd68e35c01e814      662  2016-09-11   2.4 萬 瀏覽   
60646cc365cd68e35c01e815      675  2016-09-01   1.7 萬 瀏覽   
60646cc365cd68e35c01e816    1,669  2016-06-02   3.3 萬 瀏覽   
60646cc365cd68e35c01e817      671  2014-10-25   1.8 萬 瀏覽   
60646cc365cd68e35c01e818       53  2020-05-23  8,026  瀏覽   

                                                      URL  \
_id                                                         
60646cc365cd68e35c01e814  https://icook.tw/recipes/170303   
60646cc365cd68e35c01e815  https://icook.

In [28]:
# 存一個 CSV當備份
df_merge.to_csv('./icook_sort.csv', encoding='utf-8')

In [29]:
df_merge.head()

RecipeID CategoryName         SubCategoryID  \
_id                                                                    
60646cc365cd68e35c01e814   170303         家常菜色        ['104', '602']   
60646cc365cd68e35c01e815   169048         家常菜色         ['104', '77']   
60646cc365cd68e35c01e816   155271         家常菜色  ['104', '77', '602']   
60646cc365cd68e35c01e817    90086         家常菜色        ['104', '602']   
60646cc365cd68e35c01e818   337797         家常菜色         ['104', '61']   

                               SubCategoryName RecipeName  \
_id                                                         
60646cc365cd68e35c01e814        ['烤肉', '中秋料理']     綜合雞肉串燒   
60646cc365cd68e35c01e815          ['烤肉', '宵夜']  燒烤味增秋葵透抽捲   
60646cc365cd68e35c01e816  ['烤肉', '宵夜', '中秋料理']     沙嗲烤雞肉串   
60646cc365cd68e35c01e817        ['烤肉', '中秋料理']      甜柿烤肉串   
60646cc365cd68e35c01e818          ['烤肉', '韓式']      韓式烤肉飯   

                                                                Description  \
_id                                                                           
60646cc365cd68e35c01e814  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   
60646cc365cd68e35c01e815  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...   
60646cc365cd68e35c01e816  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...   
60646cc365cd68e35c01e817   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   
60646cc365cd68e35c01e818  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...   

                                  AuthorID           Author Servings  \
_id                                                                    
60646cc365cd68e35c01e814   100002279834418              胖仙女      4人份   
60646cc365cd68e35c01e815     charminglydia              懶廚房      2人份   
60646cc365cd68e35c01e816      MrsPsKitchen  Mrs P's Kitchen      4人份   
60646cc365cd68e35c01e817   jj5colorkitchen            jj5色廚      3人份   
60646cc365cd68e35c01e818  1f2cb7b4bee5e7d2             幸福餐桌      2人份   

                         CookingTime  \
_id                                    
60646cc365cd68e35c01e814        45分鐘   
60646cc365cd68e35c01e815        20分鐘   
60646cc365cd68e35c01e816        45分鐘   
60646cc365cd68e35c01e817        30分鐘   
60646cc365cd68e35c01e818        45分鐘   

                                                                 Ingredient  \
_id                                                                           
60646cc365cd68e35c01e814  {'去骨雞腿': '4片', '起士明太子醬': '適量', '蔥白': '適量', '檸檬...   
60646cc365cd68e35c01e815  {'透抽': '1尾', '黃秋葵': '6個', '味增燒烤醬': '適量', '白芝麻'...   
60646cc365cd68e35c01e816  {'雞肉': '600克', '沙嗲醬': '1大匙', '醬油': '1小匙', '糖':...   
60646cc365cd68e35c01e817  {'火鍋白肉片': '6-7 片', '甜柿': '1 顆', '百里香': '適量', '...   
60646cc365cd68e35c01e818  {'沙朗牛肉片': '400克', '蒜': '3瓣', '洋蔥': '1顆', '蘋果':...   

                                                               CookingSteps  \
_id                                                                           
60646cc365cd68e35c01e814  [1. 雞腿肉切小塊的同時，切去皮及多餘的脂肪，取其中2/3的雞肉，加入所有的醃料拌勻，醃至...   
60646cc365cd68e35c01e815  [1. 食材大集合。, 2. 黃秋葵先在鹽上滾一滾，如此讓表面絨毛軟化，較好入口。, 3. ...   
60646cc365cd68e35c01e816  [1. 將雞肉切小塊，然後用醃料醃雞肉最少一個小時, 2. 將竹籤浸在熱水5分鐘，這可防止在...   
60646cc365cd68e35c01e817  [1. 這種豬肉片就是平常酸菜白肉鍋用的白肉片，等於沒薰過的培根肉，形狀規則，油脂豐富，比一...   
60646cc365cd68e35c01e818  [1. 以刀背將牛肉片敲打鬆軟, 2. 牛肉片切成小塊狀, 3. 將蒜、奇異果、蘋果、洋蔥放...   

                         LikeStat    Datetime    Preview  \
_id                                                        
60646cc365cd68e35c01e814      662  2016-09-11   2.4 萬 瀏覽   
60646cc365cd68e35c01e815      675  2016-09-01   1.7 萬 瀏覽   
60646cc365cd68e35c01e816    1,669  2016-06-02   3.3 萬 瀏覽   
60646cc365cd68e35c01e817      671  2014-10-25   1.8 萬 瀏覽   
60646cc365cd68e35c01e818       53  2020-05-23  8,026  瀏覽   

                                                      URL  \
_id                                                         
60646cc365cd68e35c01e814  https://icook.tw/recipes/170303   
60646cc365cd68e35c01e815  https://icook.

In [30]:
len(df_merge)

26179

In [31]:
df_merge[df_merge['AuthorID']=='iCook']


RecipeID CategoryName                SubCategoryID  \
_id                                                                           
60646da165cd68e35c01e838   221671         家常菜色  ['104', '40', '495', '602']   
60646e8e65cd68e35c01e858   122986         家常菜色         ['104', '29', '602']   
60646e8e65cd68e35c01e85e   121419         家常菜色         ['104', '39', '602']   
60646e8e65cd68e35c01e861   120708         家常菜色  ['104', '41', '449', '602']   
606473d165cd68e35c01e904   304395         家常菜色         ['491', '301', '40']   
...                           ...          ...                          ...   
6069864c65cd68e35c02808d    92501           功效                          612   
6069899065cd68e35c0280e5   274952           功效                          613   
606998f265cd68e35c0282be   253900         季節節慶                          185   
6069a23b65cd68e35c0283c7   279187         季節節慶                          137   
6069ba7865cd68e35c028607   296189         季節節慶                          602   

                                     SubCategoryName      RecipeName  \
_id                                                                    
60646da165cd68e35c01e838  ['烤肉', '豬肉', '派對', '中秋料理']          啤酒烤豬肋排   
60646e8e65cd68e35c01e858        ['烤肉', '快速', '中秋料理']         五分鐘百變串燒   
60646e8e65cd68e35c01e85e        ['烤肉', '牛肉', '中秋料理']           爐烤沙朗牛   
60646e8e65cd68e35c01e861  ['烤肉', '羊肉', '烤箱', '中秋料理']         香草堅果羊肩排   
606473d165cd68e35c01e904           ['炸物', '蛋', '豬肉']            蘇格蘭蛋   
...                                              ...             ...   
6069864c65cd68e35c02808d                          健身  【愛瘦身食堂】泡菜味噌豬肉鍋   
6069899065cd68e35c0280e5                          防疫             蔥雞湯   
606998f265cd68e35c0282be                        端午包粽             南部粽   
6069a23b65cd68e35c0283c7                          湯圓            紅白湯圓   
6069ba7865cd68e35c028607                        中秋料理           沙嗲雞肉串   

                                                                Description  \
_id                                                                           
60646da165cd68e35c01e838  一塊肋排、一手啤酒、一群朋友，這個中秋辦場肋排派對吧！🍖\n這來自另個世界的食譜配方，不僅擄...   
60646e8e65cd68e35c01e858  以往的烤肉架上總是清一色烤肉片，實在太無趣了！現在讓蔬菜跟肉做結合，讓肉更juicy蔬菜更鮮...   
60646e8e65cd68e35c01e85e  中秋派對聚會上少的就是這一道！整塊沙朗這樣處理不用手軟，主人翁的氣派大器顯露無遺！爐烤之前稍...   
60646e8e65cd68e35c01e861  烤肉絕對是中秋節最期待的事情，現在有大廚教你怎麼料理羊肩排，讓你在中秋吃得笑呵呵，平時都不敢...   
606473d165cd68e35c01e904       英國常見的家庭料理，用豬肉餡包著一整顆的半熟蛋，炸到誘人金黃色澤，一切開滿是驚喜的美味！   
...                                                                     ...   
6069864c65cd68e35c02808d  甜甜的白菜經過燉煮後，再加入韓國泡菜、日式味噌、台灣米線......融合三個國家的傳統食材後...   
6069899065cd68e35c0280e5              青蔥富含維他命B、Ｃ等營養，可以去寒、預防感冒，天冷的時候就來碗蔥雞湯吧！   
606998f265cd68e35c0282be                   粽葉包著生米與豐富配料，下鍋水煮後，口感綿密黏軟、粽葉清香四溢！   
6069a23b65cd68e35c0283c7          炸過的湯圓外皮酥香、裡面軟Q，趁熱沾裹著香氣十足的花生糖粉，超美味的傳統台式甜點！   
6069ba7865cd68e35c028607           充滿南洋風味的沙嗲醬，做為雞肉串的醃料，香濃微辣滋味，令人一串接著一串停不下來！   

                         AuthorID Author Servings CookingTime  \
_id                                                             
60646da165cd68e35c01e838    iCook    愛料理      4人份       180分鐘   
60646e8e65cd68e35c01e858    iCook    愛料理      4人份        20分鐘   
60646e8e65cd68e35c01e85e    iCook    愛料理      6人份        30分鐘   
60646e8e65cd68e35c01e861    iCook    愛料理      4人份        30分鐘   
606473d165cd68e35c01e904    iCook    愛料理      4人份        90分鐘   
...                           ...    ...      ...         ...   
6069864c65cd68e35c02808d    iCook    愛料理      3人份        30分鐘   
6069899065cd68e35c0280e5    iCook    愛料理      4人份       180分鐘   
606998f265cd68e35c0282be    iCook    愛料理     10人份       180分鐘   
6069a23b65cd68e35c0283c7    iCook    愛料理      4人份        45分鐘   
6069ba7865cd68e35c028607    iCook    愛料理      2人份        60分鐘   

                                                                 Ingredient  \
_id                                                                           
60646da165cd68e35c01e838  {'

In [32]:
df_test = df_merge.drop_duplicates(['RecipeName'], keep=False)

df_merge[~df_merge.isin(df_test['RecipeName'])]


RecipeID CategoryName         SubCategoryID  \
_id                                                                    
60646cc365cd68e35c01e814   170303         家常菜色        ['104', '602']   
60646cc365cd68e35c01e815   169048         家常菜色         ['104', '77']   
60646cc365cd68e35c01e816   155271         家常菜色  ['104', '77', '602']   
60646cc365cd68e35c01e817    90086         家常菜色        ['104', '602']   
60646cc365cd68e35c01e818   337797         家常菜色         ['104', '61']   
...                           ...          ...                   ...   
6069c28e65cd68e35c0286bd    56309         季節節慶                   602   
6069c28e65cd68e35c0286bf    55995         季節節慶                   602   
6069c28e65cd68e35c0286c0    55992         季節節慶                   602   
6069c28e65cd68e35c0286c1    55938         季節節慶                   602   
6069c28e65cd68e35c0286c2    55572         季節節慶                   602   

                               SubCategoryName RecipeName  \
_id                                                         
60646cc365cd68e35c01e814        ['烤肉', '中秋料理']        NaN   
60646cc365cd68e35c01e815          ['烤肉', '宵夜']        NaN   
60646cc365cd68e35c01e816  ['烤肉', '宵夜', '中秋料理']        NaN   
60646cc365cd68e35c01e817        ['烤肉', '中秋料理']        NaN   
60646cc365cd68e35c01e818          ['烤肉', '韓式']      韓式烤肉飯   
...                                        ...        ...   
6069c28e65cd68e35c0286bd                  中秋料理        芋頭酥   
6069c28e65cd68e35c0286bf                  中秋料理        NaN   
6069c28e65cd68e35c0286c0                  中秋料理        NaN   
6069c28e65cd68e35c0286c1                  中秋料理        蛋黃酥   
6069c28e65cd68e35c0286c2                  中秋料理        NaN   

                                                                Description  \
_id                                                                           
60646cc365cd68e35c01e814  用平底鍋或烤箱就能完成的雞肉串燒，其中照燒烤肉醬只要幾種材料組合，不必擔心市售烤肉醬有過多添...   
60646cc365cd68e35c01e815  秋葵正當季，適逢中秋節（烤肉節）腳步漸漸接近，來道『烤味增秋葵透抽』吧！\n簡單備料，有彈性...   
60646cc365cd68e35c01e816  這個充滿東南亞風味的沙嗲烤雞串，用沙嗲醬醃雞肉，然後放入烤箱烤，這可令雞肉更嫰滑多汁。再加上...   
60646cc365cd68e35c01e817   霜降吃柿子！甜柿營養豐富，卻不適合空腹吃。與肉類搭配，解油膩又清爽。簡單做法，最適合週末小派對！   
60646cc365cd68e35c01e818  百吃不膩的韓式烤肉飯，保證讓人胃口大開！無論配麵、配飯都很搭。 作法超級簡單！適合料理初學者...   
...                                                                     ...   
6069c28e65cd68e35c0286bd                    家人蒸了芋頭,但太乾了,所以我加奶油跟糖,做了酥餅,很好吃喔。   
6069c28e65cd68e35c0286bf                 愛料理食譜網中秋節到了，自己動手做月餅，美味又健康。送禮自用兩相宜喔   
6069c28e65cd68e35c0286c0             中秋節快到了,做點不一樣的月餅,剛好家裡蒸好的地瓜,把它當饀,家人都說好吃。   
6069c28e65cd68e35c0286c1                  中秋節到了,聽說外面的蛋黃酥很貴,自己做安心也沒負擔,還很好吃喔。   
6069c28e65cd68e35c0286c2                                 自製的豆沙少油少糖，吃得安心，沒負擔   

                                  AuthorID           Author Servings  \
_id                                                                    
60646cc365cd68e35c01e814   100002279834418              胖仙女      4人份   
60646cc365cd68e35c01e815     charminglydia              懶廚房      2人份   
60646cc365cd68e35c01e816      MrsPsKitchen  Mrs P's Kitchen      4人份   
60646cc365cd68e35c01e817   jj5colorkitchen            jj5色廚      3人份   
60646cc365cd68e35c01e818  1f2cb7b4bee5e7d2             幸福餐桌      2人份   
...                                    ...              ...      ...   
6069c28e65cd68e35c0286bd   100000068389648       Hank Chung      8人份   
6069c28e65cd68e35c0286bf               Obs              OBS      4人份   
6069c28e65cd68e35c0286c0   100000068389648       Hank Chung      7人份   
6069c28e65cd68e35c0286c1   100000068389648       Hank Chung     10人份   
6069c28e65cd68e35c0286c2        1023977372         Fion Tan     10人份   

                         CookingTime  \
_id                                    
60646cc365cd68e35c01e814        45分鐘   
60646cc365cd68e35c01e815        20分鐘   
60646cc365cd68e35c01e816        45分鐘   
60646cc365cd68e35c01e817        30分鐘   
60646cc365cd68e35c01e818        45分鐘   
...                              ...   
6069c28e6

In [ ]:
df_merge.head()

In [34]:
# 將資料轉成json格式存入MongoDB
jsondoc = df_merge.to_json(orient="index",force_ascii=False) # 這時資料是一個字串無法被存入MongoDB
                                                             # ex '{ '_id':{ RecipeInformation... } }'
    
import json
jsondoc = json.loads(jsondoc)  # 用 json.loads將資料轉換成 dict的型態
                               # { '_id':{ RecipeInformation... } }

In [35]:
db = client['Recipe_AfterETL']
collection = db['icook']
collection.insert_many(jsondoc.values()) # jsondoc.values 是一個 List 包住所有 RecipeInformation
                                       # ex [{Recipe:xxx, RecipeName:xxx}, {Recipe:xxx, RecipeName:xxx}]